## Imports Etc

In [233]:
import pandas as pd
## pandas 1.1.1 necessary
import numpy as np
import string 
import re
from sklearn.feature_extraction.text import TfidfVectorizer
import math
from gensim.models import Word2Vec
from plotly.graph_objects import Scatter3d
from collections import Counter

In [2]:
data = pd.read_pickle('../../delphes/data/extended_tweet_df')
look = pd.read_pickle('../../delphes/data/cleaned_tweet_df')
look = look.reset_index()

## Getting Tweets

In [121]:
from tweepy import OAuthHandler
from tweepy import API
from tweepy import Cursor
from datetime import datetime, date, time, timedelta
from collections import Counter
import sys

In [131]:
consumer_key="4BqJe9MamSVRkRXiPFlcjTxqa"
consumer_secret="TgGbjV3fAbrDJOnDQM9iD07d9rjOnkVK2N4nMiqcN3UJI8phwC"
access_token_key="871991040256999424-owsFNOcGYr7btQVKpeZDGBeET0347ot"
access_token_secret="lx7Vv0SHGICxrcxSR5mXAnOW4w26DhEcQZ1R99d1W2EIB"

auth = OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token_key, access_token_secret)
api = API(auth, wait_on_rate_limit=True)

In [138]:
import schedule
import time
account_1 = ["GreensEFA","ecrgroup","EPPGroup","GUENGL","TheProgressives","RenewEurope","IDParty_"]
account_1 = list(account_1)
all_tweets = []
content = [] 

In [139]:
def get_tweets():
    while len(account_1) > 0:
        print(len(account_1))
        if account_1[0] == 0:
            all_tweets.append(0)
            del(account_1[0])
        else: 
            content_list = []
            for tweet in Cursor(api.user_timeline,id=account_1[0],tweet_mode='extended').items(10000):
                if "retweeted_status" in dir(tweet):
                    tweet=tweet.retweeted_status.full_text
                    content_list.append(tweet)
                else:
                    tweet=tweet.full_text
                    content_list.append(tweet)
            content.append(len(content_list))
            all_tweets.append(content_list)
            del(account_1[0])
    return all_tweets

In [140]:
get_tweets()

7
6
5
4
3
2
1


[["This week the @Europarl_EN will vote on #JustTransitionFund. Due to intense lobbying, the current proposal includes subsidies for gas projects. We'll fight against this, EU must look at renewable &amp; clean alternatives to fossil fuels if we really want to face the #ClimateCrisis! https://t.co/zTb42xDIXo",
  'A #GreenWave has swept through Germany’s most-populous state North Rhine-Westphalia! In Sunday’s election @gruenenrw gained a historic result by winning 20% of votes. Most notably they won big cities like Aachen, Bonn and Cologne, and were the strongest force among young voters. https://t.co/JWybiiAPId',
  "This week the @Europarl_EN will vote on #JustTransitionFund. Due to intense lobbying, the current proposal includes subsidies for gas projects. We'll fight against this, EU must look at renewable &amp; clean alternatives to fossil fuels if we really want to face the #ClimateCrisis! https://t.co/zTb42xDIXo",
  'Last week I urged EU Member States and the European Commission t

## Translation

In [143]:
content

[3203, 3240, 3228, 3205, 3221, 3208, 2233]

In [141]:
len(all_tweets)

7

In [152]:
df_1 = pd.DataFrame(all_tweets[0])
df_2 = pd.DataFrame(all_tweets[1])
df_3 = pd.DataFrame(all_tweets[2])
df_4 = pd.DataFrame(all_tweets[3])
df_5 = pd.DataFrame(all_tweets[4])
df_6 = pd.DataFrame(all_tweets[5])
df_7 = pd.DataFrame(all_tweets[6])

In [180]:
list_df = [df_7]

In [163]:
df_5

0
0     With group leaders and UKCG, we agreed that if...
1     Next week’s #EPlenary takes place in Brussels ...
2     Today is a good day for climate justice!\n\nWe...
3     This is the letter that I sent to Commission P...
4     ⏰Now is the time for Europe to show how seriou...
...                                                 ...
3216  A Social Europe that protects us all.\nThat's ...
3217  As much as the EPP try, the Parliament was nev...
3218  Europe must invest in a sustainable future and...
3219  🇪🇸🇪🇺 Un ejemplo para todos los progresistas! N...
3220  🇪🇸🇪🇺 An example for all progressives! \n\n@san...

[3221 rows x 1 columns]

In [147]:
from googletrans import Translator
def trans_tweet(tweet):
    tra = Translator()
    return tra.translate(tweet, dest="en").text

In [158]:
res = []

In [181]:
from dask import bag, diagnostics

for df in list_df:
    premise_bag = bag.from_sequence(df[0].tolist()).map(trans_tweet)
    with diagnostics.ProgressBar():
        res.append(premise_bag.compute())

[########################################] | 100% Completed |  3min 36.7s


In [194]:
all_new = seven

### Adding Groups to Vocab

In [218]:
def sent_to_dict(sentences,dico):
    dico = {}
    count = 0
    for sentence in sentences:
        for i in sentence.split(): 
            if i in dico:
                dico[i] += 1
                count += 1
            else:
                dico[i] = 1
                count += 1
    for i,j in dico.items():
        dico[i] = j/count
    return dico

In [200]:
greens = all_new[0]
ecr = all_new[1]
epp = all_new[2]
left = all_new[3]
social = all_new[4]
renew = all_new[5]
ideology = all_new[6]

In [201]:
dict_1 = sent_to_dict(epp, dict_1)

In [205]:
dict_2 = sent_to_dict(social,dict_2)

In [208]:
dict_3 = sent_to_dict(ecr,dict_3)

In [219]:
dict_4 = sent_to_dict(renew,dict_4)
dict_6 = sent_to_dict(ideology,dict_6)
dict_7 = sent_to_dict(left,dict_7)
dict_8 = sent_to_dict(greens,dict_8)

In [223]:
len(dict_4)

20979

## Working

### Per group Pre-processing

In [3]:

Party_1 = look[look['group'] == "Group of the European People's Party (Christian Democrats)"]
Party_2 = look[look['group'] == "Group of the Progressive Alliance of Socialists and Democrats in the European Parliament"]
Party_3 = look[look['group'] == "European Conservatives and Reformists Group"]
Party_4 = look[look['group'] == "Renew Europe Group"]
Party_5 = look[look['group'] == "Non-attached Members"]
Party_6 = look[look['group'] == "Identity and Democracy Group"]
Party_7 = look[look['group'] == "Group of the European United Left - Nordic Green Left"]
Party_8 = look[look['group'] == "Group of the Greens/European Free Alliance"]

group_list = ["Group of the European People's Party (Christian Democrats)","Group of the Progressive Alliance of Socialists and Democrats in the European Parliament"\
       ,"European Conservatives and Reformists Group","Renew Europe Group","Non-attached Members",\
       "Identity and Democracy Group","Group of the European United Left - Nordic Green Left",\
       "Group of the Greens/European Free Alliance"]


In [4]:
sentences_1 = Party_1["content"].tolist()
sentences_2 = Party_2["content"].tolist()
sentences_3 = Party_3["content"].tolist()
sentences_4 = Party_4["content"].tolist()
sentences_5 = Party_5["content"].tolist()
sentences_6 = Party_6["content"].tolist()
sentences_7 = Party_7["content"].tolist()
sentences_8 = Party_8["content"].tolist()

### Per Group Dictionary

In [111]:
def sent_to_dict(sentences):
    dico = {}
    count = 0
    for sentence in sentences:
        for i in sentence.split(): 
            if i in dico:
                dico[i] += 1
                count += 1
            else:
                dico[i] = 1
                count += 1
    for i,j in dico.items():
        dico[i] = j/count
    return dico

In [6]:
sentences_list = [sentences_1,sentences_2,sentences_3,sentences_4,sentences_5,\
sentences_6,sentences_7,sentences_8]

In [112]:
dict_1 = sent_to_dict(sentences_1)
dict_2 = sent_to_dict(sentences_2)
dict_3 = sent_to_dict(sentences_3)
dict_4 = sent_to_dict(sentences_4)
dict_5 = sent_to_dict(sentences_5)
dict_6 = sent_to_dict(sentences_6)
dict_7 = sent_to_dict(sentences_7)
dict_8 = sent_to_dict(sentences_8)

In [8]:
dict_list = [dict_1,dict_2,dict_3,dict_4,dict_5,dict_6,dict_7,dict_8]

## Functions

In [9]:
def word2vec_embedding(sentences,size,min_count):
    ### build word embedding for each reviews
    word2vec_model = Word2Vec(sentences, size=size, min_count=min_count)
    return word2vec_model

In [10]:
def weight_of_words(text):
    #takes text and returns a dictionary with the word and its weight
    vectorizer = TfidfVectorizer()
    X = vectorizer.fit(text)
    weight_of_words = dict(zip(X.get_feature_names(),X.idf_))
    return weight_of_words

In [11]:
tweet_vecs = []
def weighted_words(text, weight_of_words, word2vec):
    #returns a list of n_tweets dimensions containing a (1,100) vector for each word
    check = 0
    for sentence in text:
        divided_sentence = sentence.split(' ')
        new_vecs = []
        for word in divided_sentence: 
            if word in weight_of_words.keys():
                pondered = word2vec.wv.get_vector(word).reshape(1, 100)
                check += 1
                pondered_word = pondered*weight_of_words[word]
                new_vecs.append(pondered_word)
            else:
                continue
        tweet_vecs.append(new_vecs)
    return tweet_vecs

In [12]:
sentences_train = []
for sentence in sentences_1:
    sentences_train.append(sentence.split())

In [13]:

tryout = weighted_words(sentences_1, weight_of_words(sentences_1),word2vec_embedding(sentences=sentences_train, size=100, min_count=1))



In [14]:
len(tryout)

44252

In [15]:
tweets = []
def weight_tweets(tweet_weighted_vecs):
    #returns a single (1,100) vector per tweet
    for i in range (0,len(tryout)):
        result = 0
        if len(tryout[i]) != 0:
            result = sum(tryout[i])/len(tryout[i])
            tweets.append(result.tolist())
        else: 
            tweets.append(0)
    return tweets

In [16]:
tweets = weight_tweets(tryout)

In [17]:
dict_test = {}

def df_making(tweets):
    #returns a DataFrame of n_tweets rows and 100 columns
    count = 0
    for i in range (0,len(tweets)):
        if tweets[i] != 0:
            dict_test[look["index"][i]] = tweets[i][0]
    return pd.DataFrame.from_dict(dict_test).transpose()

In [18]:
dict_test = df_making(tweets)

In [19]:
word2vec_embedding(sentences_1,size=100,min_count=1)

## Country Classif

In [237]:
countries = ['Poland', 'Bulgaria', 'Italy', 'Spain', 'Finland', 'Sweden',
       'Latvia', 'Germany', 'Greece', 'Luxembourg', 'Estonia', 'Belgium',
       'Romania', 'France', 'Denmark', 'Lithuania', 'Netherlands',
       'Slovakia', 'Hungary', 'Slovenia', 'Croatia', 'Portugal', 'Malta',
       'Cyprus', 'Ireland', 'Czechia', 'Austria']

In [240]:
countries[0].lower()

'poland'

In [247]:
for i in countries:
    f'{i}_' = look[look['country'] == i]

SyntaxError: can't assign to literal (<ipython-input-247-f6dedd807277>, line 2)

In [ ]:
sentences_1 = Party_1["content"].tolist()
sentences_2 = Party_2["content"].tolist()
sentences_3 = Party_3["content"].tolist()
sentences_4 = Party_4["content"].tolist()
sentences_5 = Party_5["content"].tolist()
sentences_6 = Party_6["content"].tolist()
sentences_7 = Party_7["content"].tolist()
sentences_8 = Party_8["content"].tolist()

## Attempt

In [20]:
analysis1 = "test"

In [25]:
Counter(dict_results).most_common(2)

[(5, 8), (4, 4)]

In [228]:
def estimator(words):
    dict_results = {}
    results = 0
    for i in dict_list:
        dict_results[results] = 0
        results += 1
    
    for i in words.split():
        results = 0
        for j in dict_list: 
            if i in j:
                dict_results[results] += j[i]
                results += 1
            else:
                results += 1    
                test = 0
    dict_results = Counter(dict_results).most_common(1)
    party_results = []
    for i in dict_results:
        party_results.append(group_list[i[0]])
    return party_results

In [70]:
word = "Hello my name is John and I love to party"

In [71]:
word = word.split()

In [61]:
word[0] + " " + word[1]

'Hello my'

In [93]:
from sklearn.model_selection import train_test_split

x_train, x_test = train_test_split(look)

In [98]:
Party_1 = x_train[x_train['group'] == "Group of the European People's Party (Christian Democrats)"]
Party_2 = x_train[x_train['group'] == "Group of the Progressive Alliance of Socialists and Democrats in the European Parliament"]
Party_3 = x_train[x_train['group'] == "European Conservatives and Reformists Group"]
Party_4 = x_train[x_train['group'] == "Renew Europe Group"]
Party_5 = x_train[x_train['group'] == "Non-attached Members"]
Party_6 = x_train[x_train['group'] == "Identity and Democracy Group"]
Party_7 = x_train[x_train['group'] == "Group of the European United Left - Nordic Green Left"]
Party_8 = x_train[x_train['group'] == "Group of the Greens/European Free Alliance"]

In [104]:
sentences_1 = Party_1["content"].tolist()
sentences_2 = Party_2["content"].tolist()
sentences_3 = Party_3["content"].tolist()
sentences_4 = Party_4["content"].tolist()
sentences_5 = Party_5["content"].tolist()
sentences_6 = Party_6["content"].tolist()
sentences_7 = Party_7["content"].tolist()
sentences_8 = Party_8["content"].tolist()

In [114]:
def sent_to_dict(sentences):
    dico = {}
    count = 0
    for sentence in sentences:
        dict_attempt = []
        sentences = sentence.split()
        for j in range(1,len(sentences),2):
            x = (str(sentences[j-1]) + " " + str(sentences[j]))
            dict_attempt.append(x) 
        for i in dict_attempt:
            if i in dico:
                dico[i] += 1
                count += 1
            else:
                dico[i] = 1
                count += 1
    for i,j in dico.items():
        dico[i] = j/count
    return dico

In [108]:
sentences_list = [sentences_1,sentences_2,sentences_3,sentences_4,sentences_5,\
sentences_6,sentences_7,sentences_8]

In [116]:
dict_10 = sent_to_dict(sentences_1)
dict_20 = sent_to_dict(sentences_2)
dict_30 = sent_to_dict(sentences_3)
dict_40 = sent_to_dict(sentences_4)
dict_50 = sent_to_dict(sentences_5)
dict_60 = sent_to_dict(sentences_6)
dict_70 = sent_to_dict(sentences_7)
dict_80 = sent_to_dict(sentences_8)

In [88]:
start = 0
dict_attempt = []
for i in sentences_1: 
    sentences = i.split()
    for j in range(1,len(sentences),2):
        x = (str(sentences[j-1]) + " " + str(sentences[j]))
        dict_attempt.append(x)   

In [117]:
def estimator_2(words):
    dict_results = {}
    results = 0
    for i in dict_list:
        dict_results[results] = 0
        results += 1
    
    for i in words.split():
        results = 0
        for j in dict_list: 
            if i in j:
                dict_results[results] += j[i]
                results += 1
            else:
                results += 1    
                test = 0
    dict_results = Counter(dict_results).most_common(1)
    party_results = []
    for i in dict_results:
        party_results.append(group_list[i[0]])
    return party_results

In [120]:
estimator_2(x_train["content"])

AttributeError: 'Series' object has no attribute 'split'

## Evaluation

In [248]:
import requests
pip 

In [252]:
diffbot = diffbot.Client()
token = API_TOKEN
url = "https://www.lemonde.fr/planete/article/2020/09/10/covid-19-emmanuel-macron-promet-de-donner-vendredi-de-la-visibilite-sur-les-prochaines-semaines_6051673_3244.html"
api = "article"
response = diffbot.request(url, token, api, fields=['title', 'type'])
print ("\nPrinting response:\n")
pp = pprint.PrettyPrinter(indent=4)
print (pp.pprint(response))

NameError: name 'diffbot' is not defined

In [229]:
score = 0
results = 0
for i in range(0,len(look["content"])):
    if look["group"][i] in estimator(look["content"][i]):
        score += 1 
        results += 1
    else:
        results += 1
    print(score,results)

1 1
1 2
1 3
1 4
1 5
1 6
1 7
1 8
1 9
1 10
1 11
1 12
1 13
1 14
1 15
1 16
1 17
1 18
1 19
2 20
2 21
3 22
3 23
3 24
3 25
3 26
3 27
3 28
3 29
3 30
3 31
3 32
3 33
3 34
3 35
3 36
3 37
3 38
3 39
3 40
3 41
3 42
3 43
3 44
3 45
3 46
3 47
3 48
3 49
3 50
3 51
3 52
4 53
4 54
4 55
5 56
5 57
5 58
6 59
6 60
6 61
6 62
6 63
6 64
6 65
6 66
6 67
6 68
6 69
6 70
6 71
6 72
6 73
6 74
6 75
6 76
6 77
6 78
6 79
6 80
6 81
6 82
6 83
6 84
7 85
8 86
8 87
8 88
8 89
8 90
8 91
8 92
8 93
8 94
8 95
8 96
8 97
8 98
8 99
8 100
8 101
8 102
8 103
8 104
8 105
8 106
8 107
9 108
10 109
10 110
11 111
11 112
11 113
11 114
11 115
11 116
11 117
11 118
11 119
11 120
12 121
12 122
12 123
12 124
12 125
13 126
13 127
13 128
13 129
13 130
13 131
14 132
14 133
14 134
14 135
14 136
14 137
14 138
14 139
15 140
15 141
15 142
15 143
15 144
15 145
15 146
15 147
15 148
15 149
15 150
15 151
15 152
15 153
16 154
16 155
16 156
17 157
17 158
17 159
17 160
17 161
17 162
17 163
18 164
18 165
18 166
18 167
18 168
19 169
19 170
19 171
19 172
19 173
19 17

275 1322
276 1323
276 1324
277 1325
278 1326
279 1327
280 1328
280 1329
281 1330
281 1331
282 1332
282 1333
283 1334
283 1335
284 1336
285 1337
286 1338
286 1339
286 1340
286 1341
287 1342
288 1343
288 1344
289 1345
290 1346
291 1347
291 1348
291 1349
291 1350
292 1351
293 1352
293 1353
294 1354
295 1355
295 1356
295 1357
295 1358
295 1359
296 1360
297 1361
297 1362
298 1363
298 1364
299 1365
300 1366
300 1367
300 1368
301 1369
301 1370
302 1371
303 1372
303 1373
304 1374
305 1375
305 1376
306 1377
307 1378
307 1379
307 1380
307 1381
308 1382
308 1383
308 1384
308 1385
308 1386
308 1387
309 1388
309 1389
309 1390
310 1391
310 1392
310 1393
311 1394
312 1395
312 1396
312 1397
313 1398
313 1399
314 1400
315 1401
315 1402
315 1403
316 1404
317 1405
317 1406
317 1407
318 1408
318 1409
319 1410
319 1411
320 1412
320 1413
321 1414
322 1415
323 1416
323 1417
324 1418
325 1419
325 1420
325 1421
326 1422
326 1423
326 1424
327 1425
328 1426
329 1427
329 1428
329 1429
329 1430
329 1431
329 1432
3

790 2964
790 2965
790 2966
790 2967
790 2968
790 2969
790 2970
790 2971
790 2972
790 2973
790 2974
790 2975
791 2976
792 2977
793 2978
793 2979
794 2980
794 2981
794 2982
795 2983
795 2984
795 2985
796 2986
796 2987
796 2988
797 2989
797 2990
798 2991
798 2992
798 2993
799 2994
799 2995
799 2996
799 2997
799 2998
799 2999
800 3000
800 3001
800 3002
800 3003
800 3004
800 3005
800 3006
800 3007
800 3008
800 3009
800 3010
800 3011
800 3012
800 3013
800 3014
800 3015
800 3016
800 3017
800 3018
800 3019
800 3020
800 3021
800 3022
801 3023
802 3024
802 3025
802 3026
802 3027
803 3028
803 3029
803 3030
803 3031
803 3032
803 3033
803 3034
803 3035
803 3036
803 3037
803 3038
803 3039
803 3040
803 3041
803 3042
804 3043
805 3044
806 3045
807 3046
807 3047
807 3048
807 3049
807 3050
807 3051
807 3052
807 3053
807 3054
807 3055
807 3056
807 3057
807 3058
808 3059
808 3060
808 3061
808 3062
808 3063
808 3064
808 3065
808 3066
808 3067
809 3068
809 3069
809 3070
809 3071
809 3072
809 3073
809 3074
8

1123 4404
1124 4405
1125 4406
1125 4407
1126 4408
1126 4409
1126 4410
1126 4411
1126 4412
1126 4413
1126 4414
1127 4415
1127 4416
1127 4417
1127 4418
1128 4419
1128 4420
1129 4421
1129 4422
1130 4423
1130 4424
1131 4425
1131 4426
1131 4427
1131 4428
1132 4429
1132 4430
1132 4431
1133 4432
1133 4433
1134 4434
1135 4435
1135 4436
1135 4437
1135 4438
1135 4439
1136 4440
1136 4441
1137 4442
1137 4443
1137 4444
1137 4445
1137 4446
1138 4447
1138 4448
1139 4449
1139 4450
1139 4451
1139 4452
1139 4453
1139 4454
1140 4455
1141 4456
1142 4457
1142 4458
1142 4459
1142 4460
1142 4461
1143 4462
1144 4463
1145 4464
1145 4465
1146 4466
1146 4467
1146 4468
1147 4469
1147 4470
1147 4471
1147 4472
1148 4473
1148 4474
1148 4475
1149 4476
1150 4477
1151 4478
1151 4479
1152 4480
1153 4481
1153 4482
1153 4483
1154 4484
1154 4485
1155 4486
1155 4487
1155 4488
1155 4489
1155 4490
1156 4491
1157 4492
1158 4493
1158 4494
1158 4495
1158 4496
1158 4497
1158 4498
1159 4499
1160 4500
1160 4501
1161 4502
1161 4503


1613 5990
1614 5991
1615 5992
1616 5993
1617 5994
1617 5995
1617 5996
1617 5997
1617 5998
1618 5999
1619 6000
1619 6001
1620 6002
1620 6003
1621 6004
1622 6005
1622 6006
1623 6007
1624 6008
1624 6009
1625 6010
1625 6011
1626 6012
1627 6013
1628 6014
1629 6015
1629 6016
1630 6017
1630 6018
1631 6019
1631 6020
1631 6021
1631 6022
1631 6023
1632 6024
1632 6025
1632 6026
1632 6027
1632 6028
1632 6029
1632 6030
1632 6031
1633 6032
1633 6033
1633 6034
1633 6035
1633 6036
1633 6037
1633 6038
1633 6039
1633 6040
1633 6041
1633 6042
1633 6043
1633 6044
1633 6045
1633 6046
1633 6047
1633 6048
1633 6049
1633 6050
1633 6051
1633 6052
1633 6053
1633 6054
1633 6055
1633 6056
1633 6057
1633 6058
1633 6059
1633 6060
1633 6061
1634 6062
1634 6063
1634 6064
1634 6065
1634 6066
1634 6067
1634 6068
1634 6069
1634 6070
1634 6071
1634 6072
1634 6073
1634 6074
1634 6075
1634 6076
1634 6077
1634 6078
1634 6079
1634 6080
1634 6081
1634 6082
1634 6083
1635 6084
1636 6085
1636 6086
1636 6087
1636 6088
1636 6089


...

29368 130881
29368 130882
29368 130883
29368 130884
29368 130885
29368 130886
29368 130887
29368 130888
29368 130889
29368 130890
29368 130891
29368 130892
29368 130893
29368 130894
29368 130895
29368 130896
29368 130897
29368 130898
29368 130899
29368 130900
29368 130901
29368 130902
29368 130903
29369 130904
29369 130905
29369 130906
29369 130907
29370 130908
29370 130909
29370 130910
29370 130911
29370 130912
29370 130913
29371 130914
29371 130915
29371 130916
29371 130917
29371 130918
29371 130919
29371 130920
29371 130921
29371 130922
29371 130923
29371 130924
29371 130925
29371 130926
29371 130927
29371 130928
29371 130929
29372 130930
29372 130931
29372 130932
29372 130933
29372 130934
29372 130935
29372 130936
29372 130937
29372 130938
29373 130939
29373 130940
29373 130941
29373 130942
29373 130943
29373 130944
29373 130945
29373 130946
29374 130947
29374 130948
29374 130949
29374 130950
29374 130951
29374 130952
29374 130953
29374 130954
29374 130955
29374 130956
29374 130957

29478 131669
29478 131670
29479 131671
29479 131672
29479 131673
29480 131674
29481 131675
29481 131676
29481 131677
29481 131678
29482 131679
29482 131680
29482 131681
29483 131682
29483 131683
29484 131684
29485 131685
29486 131686
29486 131687
29486 131688
29487 131689
29487 131690
29488 131691
29488 131692
29488 131693
29489 131694
29489 131695
29489 131696
29490 131697
29491 131698
29492 131699
29492 131700
29492 131701
29492 131702
29493 131703
29493 131704
29493 131705
29493 131706
29493 131707
29494 131708
29495 131709
29495 131710
29496 131711
29496 131712
29497 131713
29497 131714
29497 131715
29497 131716
29498 131717
29499 131718
29499 131719
29499 131720
29499 131721
29500 131722
29500 131723
29500 131724
29500 131725
29500 131726
29500 131727
29501 131728
29502 131729
29502 131730
29502 131731
29503 131732
29504 131733
29505 131734
29506 131735
29506 131736
29506 131737
29506 131738
29506 131739
29506 131740
29507 131741
29507 131742
29508 131743
29508 131744
29508 131745

29715 132519
29715 132520
29715 132521
29715 132522
29715 132523
29715 132524
29715 132525
29715 132526
29715 132527
29716 132528
29716 132529
29716 132530
29716 132531
29716 132532
29716 132533
29716 132534
29716 132535
29716 132536
29716 132537
29716 132538
29716 132539
29716 132540
29716 132541
29716 132542
29716 132543
29716 132544
29716 132545
29716 132546
29716 132547
29716 132548
29716 132549
29716 132550
29716 132551
29716 132552
29716 132553
29716 132554
29716 132555
29716 132556
29717 132557
29717 132558
29717 132559
29717 132560
29717 132561
29718 132562
29718 132563
29719 132564
29719 132565
29720 132566
29720 132567
29720 132568
29721 132569
29721 132570
29722 132571
29722 132572
29722 132573
29722 132574
29722 132575
29722 132576
29722 132577
29723 132578
29723 132579
29723 132580
29723 132581
29723 132582
29723 132583
29723 132584
29723 132585
29723 132586
29723 132587
29724 132588
29724 132589
29724 132590
29724 132591
29724 132592
29724 132593
29724 132594
29724 132595

29805 133330
29806 133331
29806 133332
29806 133333
29806 133334
29806 133335
29806 133336
29806 133337
29806 133338
29806 133339
29806 133340
29806 133341
29806 133342
29806 133343
29806 133344
29806 133345
29806 133346
29806 133347
29806 133348
29806 133349
29806 133350
29806 133351
29806 133352
29806 133353
29806 133354
29806 133355
29806 133356
29806 133357
29806 133358
29806 133359
29806 133360
29806 133361
29806 133362
29806 133363
29806 133364
29807 133365
29808 133366
29808 133367
29809 133368
29809 133369
29810 133370
29810 133371
29810 133372
29811 133373
29811 133374
29811 133375
29811 133376
29811 133377
29811 133378
29811 133379
29812 133380
29813 133381
29813 133382
29814 133383
29814 133384
29815 133385
29815 133386
29815 133387
29815 133388
29816 133389
29816 133390
29816 133391
29816 133392
29816 133393
29816 133394
29817 133395
29818 133396
29818 133397
29818 133398
29818 133399
29819 133400
29820 133401
29821 133402
29821 133403
29821 133404
29821 133405
29822 133406

30154 134143
30154 134144
30155 134145
30155 134146
30155 134147
30156 134148
30156 134149
30156 134150
30156 134151
30156 134152
30156 134153
30156 134154
30156 134155
30156 134156
30156 134157
30156 134158
30156 134159
30156 134160
30157 134161
30157 134162
30158 134163
30158 134164
30159 134165
30159 134166
30159 134167
30159 134168
30160 134169
30161 134170
30161 134171
30161 134172
30161 134173
30161 134174
30161 134175
30161 134176
30161 134177
30161 134178
30162 134179
30162 134180
30163 134181
30164 134182
30164 134183
30164 134184
30165 134185
30166 134186
30167 134187
30167 134188
30167 134189
30168 134190
30168 134191
30168 134192
30168 134193
30168 134194
30169 134195
30169 134196
30169 134197
30169 134198
30169 134199
30169 134200
30169 134201
30169 134202
30170 134203
30170 134204
30170 134205
30170 134206
30171 134207
30172 134208
30173 134209
30174 134210
30175 134211
30175 134212
30175 134213
30175 134214
30175 134215
30175 134216
30176 134217
30176 134218
30176 134219

In [231]:
results

134724

In [232]:
score/results

0.22461476797007215